In [1]:
#//*** GEOPANDAS sources
#https://jcutrer.com/python/learn-geopandas-plotting-usmaps
#https://www.census.gov/geographies/mapping-files/time-series/geo/carto-boundary-file.html
#https://towardsdatascience.com/lets-make-a-map-using-geopandas-pandas-and-matplotlib-to-make-a-chloropleth-map-dddc31c1983d
#https://geopandas.org/docs/user_guide/mapping.html

#//*** Build Custom Color Gradients
#https://coolors.co/gradient-palette/ffffff-e0472b?number=9

#//*** pandas_bokeh
#//*** https://pythonawesome.com/bokeh-plotting-backend-for-pandas-and-geopandas/

### CDC Community Transmission Guidelines

https://covid.cdc.gov/covid-data-tracker/#county-view



![](transmission_risk.png)

In [27]:
import os
import sys
# //*** Imports and Load Data
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import requests
#//*** Use the whole window in the IPYNB editor
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

import time 
import random
from PIL import Image

import shutil
import json

import geopandas as gpd

import pandas_bokeh
pandas_bokeh.output_notebook()


from matplotlib.colors import ListedColormap, LinearSegmentedColormap

#//*** Maximize columns and rows displayed by pandas
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', None)

pd.set_option('display.width', 200)

#df_list = []

#from sklearn import linear_model
#from math import sqrt
#from sklearn.metrics import mean_squared_error

#//*** Filenames for Caching files locally
attrib_confirm_filename = "attrib_confirm_df.dat.zip"
attrib_death_filename =  "attrib_death_df.dat.zip"
vaccine_data_filename = "us_vaccination.csv"
all_dates_filename = "all_dates.json"


Loading BokehJS ...

In [3]:
#"https://github.com/CSSEGISandData/COVID-19/raw/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_US.csv"

In [29]:
vax_df = pd.read_csv(vaccine_data_filename)
vax_df

Date  MMWR_week Location  Distributed  Distributed_Janssen  Distributed_Moderna  Distributed_Pfizer  Distributed_Unk_Manuf  Dist_Per_100K  Distributed_Per_100k_12Plus  \
0      09/20/2021         38       CT      5546085               256200              2248620             3041265                      0         155558                       178563   
1      09/20/2021         38       FM        83600                10200                71600                1800                      0          80662                        94454   
2      09/20/2021         38       CO      8061375               352400              3247960             4461015                      0         139985                       163316   
3      09/20/2021         38      VA2      6385490               522400              3047680             2815410                      0              0                            0   
4      09/20/2021         38       DE      1529335                65800               609420              854115                      0         157054                       182106   
...           ...        ...      ...          ...                  ...                  ...                 ...                    ...            ...                          ...   
18228  12/13/2020         51      LTC            0                    0                    0                   0                      0              0                            0   
18229  12/13/2020         51       MP         4875                    0                    0                   0                      0           8570                            0   
18230  12/13/2020         51       AS         3900                    0                    0                   0                      0           7003                            0   
18231  12/13/2020         51       US        13650                    0                    0                   0                      0              4                            0   
18232  12/13/2020         51       GU         3900                    0                    0                   0                      0           2353                            0   

       Distributed_Per_100k_18Plus  Distributed_Per_100k_65Plus  Administered  Administered_12Plus  Administered_18Plus  Administered_65Plus  Administered_Janssen  Administered_Moderna  \
0                           195433                       879990       4964279              4962561              4588593              1212869                203150               1850868   
1                           103560                       476055         70007                69993                69277                 5550                 11429                 57853   
2                           179173                       956940       7058569              7038481              6546377              1516091                264161               2806298   
3                                0                            0       5633417              5633256              5630555              2938120                215774               2888656   
4                           198565                       809575       1182145              1181941              1105411               351396                 50194                458547   
...                            ...                          ...           ...                  ...                  ...                  ...                   ...                   ...   
18228                            0                            0             0                    0                    0                    0                     0                     0   
18229                            0                            0             0                    0                    0                    0                     0                     0   
18230                            0                            0             0                    0                    0     

In [28]:

#CDC Data: https://catalog.data.gov/dataset/covid-19-vaccinations-in-the-united-statescounty

try:
    #response = requests.get("https://data.cdc.gov/api/views/8xkx-amqh/rows.csv?accessType=DOWNLOAD")
    response = requests.get("https://data.cdc.gov/api/views/unsk-b7fc/rows.csv?accessType=DOWNLOAD")
    if response.ok:
        print("Vaccination Data Downloading")
        f = open(vaccine_data_filename, "w")
        f.write(response.text)
        f.close()
        print("US Vaccination Data Written to file.")
except:
    print("US Vaccine Data: Trouble Downloading From CDC")

Vaccination Data Downloading
US Vaccination Data Written to file.


In [4]:
#//************************************************************************
#//*** If True, will rely on locally stored files
#//*** If False, will Download current data and rebuild all data sets
#//*** Should only be set to False if Data needs to be updated
#//************************************************************************
use_cached_files = True

confirmed_data_filename = "z_us_confirmed.csv"
death_data_filename = "z_us_death_cases.csv"

#//***********************************************************************************************
#//*** California COVID Data website:
#//**************************************
#//*** https://data.chhs.ca.gov/dataset/covid-19-time-series-metrics-by-county-and-state
#//***********************************************************************************************

#//*** Download California Current COVID Demograohic Data
if not use_cached_files:
    try:
        response = requests.get("https://github.com/CSSEGISandData/COVID-19/raw/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_US.csv")
        if response.ok:
            print("US Confirmed Data Downloaded")
            f = open(confirmed_data_filename, "w")
            f.write(response.text)
            f.close()
            print("US Confirmed Data Written to file.")
    except:
        print("US Confirmed Data: Trouble Downloading From Johns Hopkins Github")

    try:
        response = requests.get("https://github.com/CSSEGISandData/COVID-19/raw/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv")
        if response.ok:
            print("US Deaths Data Downloaded")
            f = open(death_data_filename, "w")
            f.write(response.text)
            f.close()
            print("US Death Data Written to file.")
    except:
        print("US Death Data: Trouble Downloading From Johns Hopkins Github")
#confirm_df = pd.read_csv(confirmed_data_filename, dtype={"FIPS":np.int32})


In [5]:
if use_cached_files:
    #//*** Load Locally stored data
    attrib_confirm_df = pd.read_pickle(attrib_confirm_filename)
    print("Loading Cached: confirm_df")
    attrib_death_df = pd.read_pickle(attrib_death_filename)
    print("Loading Cached: death_df")
    
        
        # Read all dates JSON
    with open(all_dates_filename, "r") as infile:
        all_dates = json.loads(infile.read())['all_dates']
    print("Loading Cached: all_dates")
else:
    print("Re-Building Data...")
    #//**** Load Confirmed Data
    confirm_df = pd.read_csv(confirmed_data_filename)
    confirm_df = confirm_df.dropna(subset=["FIPS"])

    #//**** Load death Data
    death_df = pd.read_csv(death_data_filename)
    death_df = death_df[death_df["Admin2"] != "Unassigned"]
    death_df = death_df.dropna(subset=["FIPS"])

    #//*** Rename Columns to sync dataframes by FIPS/GEOID

    ren_cols = {
        "FIPS" : "GEOID"
    }

    #//*********************************
    #//*** Rename Confirmed Cols
    #//*********************************

    #//*** Get columns
    cols = np.array(confirm_df.columns)

    #//*** Rplace Values
    for find_col,replace_col in ren_cols.items():
        cols = np.where(cols == find_col,replace_col,cols)

    #//*** update columns
    confirm_df.columns = cols

    #//*********************************
    #//*** Rename Death Cols
    #//*********************************
    #//*** Get columns
    cols = np.array(death_df.columns)

    #//*** Replace Values
    for find_col,replace_col in ren_cols.items():
        cols = np.where(cols == find_col,replace_col,cols)

    #//*** update columns
    death_df.columns = cols


    confirm_df["GEOID"] = confirm_df["GEOID"].astype(np.int)
    death_df["GEOID"] =   death_df["GEOID"].astype(np.int)

    #//*** US States Only. Lose the Territories
    confirm_df = confirm_df[confirm_df['iso3'] == 'USA']
    death_df = death_df[death_df['iso3'] == 'USA']


    #//*** Get Shape File
    states = gpd.read_file('maps\cb_2018_us_county_20m.shp')

    #//*** Keep the important Columns
    states = states[['STATEFP','GEOID','NAME','geometry']]


    states['GEOID'] = states['GEOID'].astype(int)

    #//*** Merge with Shapes
    confirm_df = states.merge(confirm_df,left_on="GEOID",right_on="GEOID")
    death_df = states.merge(death_df,left_on="GEOID",right_on="GEOID")

    #//*** Remove Extra Columns
    rem_cols = ['iso2','iso3','code3',"Admin2","Country_Region","Lat","Long_","UID"]

    cols = list(confirm_df.columns)

    for col in rem_cols:
        cols.remove(col)

    confirm_df = confirm_df[cols]

    cols = list(death_df.columns)

    for col in rem_cols:
        cols.remove(col)

    death_df = death_df[cols]

    #//*** Convert Cumulative Cases to Daily Cases
    confirm_df[confirm_df.columns[6:]] = confirm_df[confirm_df.columns[6:]].diff(axis = 1, periods = 1)
    death_df[death_df.columns[7:]]     = death_df[death_df.columns[7:]].diff(axis = 1, periods = 1)

    #//*** Convert to 7-day Rolling Mean of New Cases
    confirm_df[confirm_df.columns[6:]] = confirm_df[confirm_df.columns[6:]].rolling(7,axis=1).mean()
    death_df[death_df.columns[7:]] = death_df[death_df.columns[7:]].rolling(7,axis=1).mean()


    #//*** Remove the single na column
    confirm_df = confirm_df.dropna(axis=1)
    death_df = death_df.dropna(axis=1)



    #//**** Merge Population with confirm. Pop_df is first to keep population stats away from the data columns that are added sequentially every day
    confirm_df = confirm_df.merge(death_df[['GEOID','Population']].copy(),left_on="GEOID",right_on="GEOID")

    #//*** Generate population 100k values
    confirm_df['pop_100k'] = confirm_df['Population'] / 100000
    death_df['pop_100k'] = death_df['Population'] / 100000

    #//*** Filter out Hawaii and Alaska
    confirm_df = confirm_df[confirm_df["Province_State"] != "Hawaii"]
    confirm_df = confirm_df[confirm_df["Province_State"] != "Alaska"]

    death_df = death_df[death_df["Province_State"] != "Hawaii"]
    death_df = death_df[death_df["Province_State"] != "Alaska"]
    
    print("Done!")


Loading Cached: confirm_df
Loading Cached: death_df
Loading Cached: all_dates


In [6]:
#//*** Build Case attributes, if not using cached values
if not use_cached_files:

    #//*** Split Attribute Columns from Data Columns
    attrib_confirm_df = confirm_df[confirm_df.columns[:6]].copy()

    data_confirm_df = confirm_df[confirm_df.columns[6:]].copy()

    #//*** Move Last two Data Cols to attrib_confirm_df
    last_cols = data_confirm_df.columns[-2:]

    for col in last_cols:
        #//*** Add Column to attrib_confirm_df
        attrib_confirm_df[col] = data_confirm_df[col]

        #//*** Delete Column from data_confirm_df
        del data_confirm_df[col]


    #//*** Split Death Columns into attrib_death_df and data_death_df
    attrib_death_df = death_df[death_df.columns[:7]].copy()

    data_death_df = death_df[death_df.columns[7:]].copy()

    #//*** Move Last two Data Cols to attrib_confirm_df
    last_cols = death_df.columns[-1:]

    for col in last_cols:
        #//*** Add Column to attrib_confirm_df
        attrib_death_df[col] = data_death_df[col]

        #//*** Delete Column from data_confirm_df
        del data_death_df[col]



    #//*** Rename Attrib Columns for Cleanliness and Vanity
    ren_cols = {
        "POPESTIMATE" : "Population",
        "Combined_Key" : "Loc",
        "STNAME" : "State",
        "CTYNAME" : "County",
        #"9/17/21" : "New_Cases_9/17/21"
    }

    #//*** Get columns
    cols = np.array(attrib_confirm_df.columns)

    #//*** Replace Values
    for find_col,replace_col in ren_cols.items():
        cols = np.where(cols == find_col,replace_col,cols)

    #//*** Change Column Names    
    attrib_confirm_df.columns = cols


    #//**** clean Combined County Names
    attrib_confirm_df['Loc'] = attrib_confirm_df['Loc'].str.replace(", US","")

    #//**** Rename DEATH_DF Columns
    #//*** Get columns
    cols = np.array(attrib_death_df.columns)

    #//*** Replace Values
    for find_col,replace_col in ren_cols.items():
        cols = np.where(cols == find_col,replace_col,cols)

    #//*** Change Column Names    
    attrib_death_df.columns = cols


    #//**** clean Combined County Names
    attrib_confirm_df['Loc'] = attrib_confirm_df['Loc'].str.replace(", US","")
    attrib_death_df['Loc'] = attrib_death_df['Loc'].str.replace(", US","")


    #//*** Clean Attributes
    attrib_confirm_df

    #//**********************
    #//*** Build Daily Data
    #//**********************

    #//*** Get All Dates
    all_dates = list(data_confirm_df.columns)
    all_dates

    start_time = time.time()
    print(f"Begin Building Case Attributes...")


    #//*** Loop through each date and build daily derived Data
    for date in all_dates:

        #//*** Add New Cases for each Date
        col = f"{date}_New_Cases"
        attrib_confirm_df[col] = data_confirm_df[date].astype(int)
        
        col = f"{date}_New_Deaths"
        attrib_death_df[col]   = data_death_df[date].astype(int)

        #//*** Calculate New Cases Per 100k
        col = f"{date}_New_Cases_per_100k"
        attrib_confirm_df[col] = (data_confirm_df[date] / attrib_confirm_df['pop_100k']).astype(int)
        
        death_col = f"{date}_New_Deaths_per_100k"
        attrib_death_df[death_col] =   (data_death_df[date] / attrib_death_df['pop_100k']).astype(int)

        #//*** Build Scaled 100k cases (min=0, max=100)
        #//*** Make a copy to date_scaled_100k
        attrib_confirm_df[f"{date}_scaled_100k"] = attrib_confirm_df[col]
        attrib_death_df[f"{date}_scaled_100k"]   = attrib_death_df[death_col]


        #//*** Replace Values < 0 with 0. Negative values are due to adjustments from previous day values
        attrib_confirm_df.loc[attrib_confirm_df[f"{date}_scaled_100k"] < 0,f"{date}_scaled_100k"]=0
        attrib_death_df.loc[attrib_death_df[f"{date}_scaled_100k"] < 0,f"{date}_scaled_100k"]=0

        #//*** Replace Values < 0 with 0. Negative values are due to adjustments from previous day values
        #//*** Set Maximum community transmission to 100. This is the Max value on the CDC Scale, and it quiets this
        attrib_confirm_df.loc[attrib_confirm_df[f"{date}_scaled_100k"] > 100,f"{date}_scaled_100k"]=100
        attrib_death_df.loc[attrib_death_df[f"{date}_scaled_100k"] > 100,f"{date}_scaled_100k"]=100

    #//*** Everything to a file
    attrib_confirm_df.to_pickle(attrib_confirm_filename)
    attrib_death_df.to_pickle(attrib_death_filename)


    # Writing to sample.json
    with open(all_dates_filename, "w") as outfile:
        outfile.write(json.dumps({"all_dates" : all_dates}))

print("Done!")

Done!


In [7]:
#//********************************************
#//*** Build Confirmed Historical Slider Plot
#//********************************************
plot_df = attrib_confirm_df.copy()
    

slider_columns = [f"{x}_scaled_100k" for x in all_dates]

slider_range = all_dates
slider_range = [i for i in range(0,len(all_dates))]

#hover_cols = ["Population","Loc"]
#for x in [x*(int(len(all_dates)/8)) for x in range(1,9)]:
#    hover_cols.append(f"{all_dates[x]}_New_Cases")
#    hover_cols.append(f"{all_dates[x]}_New_Cases_per_100k")
hover_cols = ["Population","Loc"]

slider_name = "COVID Day"

out_confirm_historical = plot_df.plot_bokeh(
    figsize=(1268, 1024),
    #category="scale_100k",
    title = f"U.S. COVID Prevalence (Cases per 100k Population): {all_dates[0]} - {all_dates[-1]}",
    slider=slider_columns,
    slider_range = slider_range,
    slider_name = slider_name,
    #title = "TITLE HERE",
    #category="New_Cases_9/17/21",
    #simplify_shapes=5000,
    #dropdown=["POPESTIMATE2010", "POPESTIMATE2017"],
    colormap="Viridis",
    #colormap="Inferno",
    hovertool_columns=hover_cols,
    show_figure=False,
    return_html=True
    #tile_provider_url=r"http://c.tile.stamen.com/watercolor/{Z}/{X}/{Y}.jpg"
    )
#plt.show()

In [8]:
#//********************************************
#//*** Build Confirmed Current Stats Plot
#//********************************************
plot_df = attrib_confirm_df[(list(attrib_confirm_df.columns[:8]) + list(attrib_confirm_df.columns[-3:]))].copy()

category = plot_df.columns[-1]

hover_cols = (["Loc","Population"] + list(plot_df.columns[-3:-1]))
#hover_cols = ["Loc","Population"]
out_confirm_latest = plot_df.plot_bokeh(
    figsize=(1268, 1024),
    category=category,
    title = f"Current COVID New Case Prevalence (per 100k population) 7-Day Average\nUpdated: {all_dates[-1]}",
    #category="New_Cases_9/17/21",
    #simplify_shapes=5000,
    #dropdown=["POPESTIMATE2010", "POPESTIMATE2017"],
    colormap="Viridis",
    #colormap="Inferno",
    hovertool_columns=hover_cols,
    show_figure=False,
    return_html=True
    #tile_provider_url=r"http://c.tile.stamen.com/watercolor/{Z}/{X}/{Y}.jpg"
    )

In [9]:
plot_df

STATEFP  GEOID      NAME                                           geometry  Province_State                     Loc  Population  pop_100k  9/19/21_New_Cases  9/19/21_New_Cases_per_100k  \
0         37  37017    Bladen  POLYGON ((-78.90200 34.83527, -78.79960 34.850...  North Carolina  Bladen, North Carolina       32722   0.32722                 19                          59   
1         37  37167    Stanly  POLYGON ((-80.49737 35.20210, -80.29542 35.502...  North Carolina  Stanly, North Carolina       62806   0.62806                 69                         110   
2         39  39153    Summit  POLYGON ((-81.68699 41.13596, -81.68495 41.277...            Ohio            Summit, Ohio      541013   5.41013                196                          36   
3         42  42113  Sullivan  POLYGON ((-76.81373 41.59003, -76.22014 41.541...    Pennsylvania  Sullivan, Pennsylvania        6066   0.06066                  4                          68   
4         48  48459    Upshur  POLYGON ((-95.15274 32.66095, -95.15211 32.902...           Texas           Upshur, Texas       41753   0.41753                 33                          79   
...      ...    ...       ...                                                ...             ...                     ...         ...       ...                ...                         ...   
3137      22  22003     Allen  POLYGON ((-93.13029 30.59789, -92.97917 30.598...       Louisiana        Allen, Louisiana       25627   0.25627                 14                          56   
3138      38  38005    Benson  POLYGON ((-99.84661 48.37130, -99.49292 48.370...    North Dakota    Benson, North Dakota        6832   0.06832                  3                          46   
3139      31  31159    Seward  POLYGON ((-97.36812 41.04695, -96.91094 41.046...        Nebraska        Seward, Nebraska       17284   0.17284                  0                           0   
3140      37  37023     Burke  POLYGON ((-81.90665 35.88338, -81.94319 35.960...  North Carolina   Burke, North Carolina       90485   0.90485                104                         115   
3141      13  13261    Sumter  POLYGON ((-84.43301 32.04196, -84.43121 32.134...         Georgia         Sumter, Georgia       29524   0.29524                 19                          66   

      9/19/21_scaled_100k  
0                      59  
1                     100  
2                      36  
3                      68  
4                      79  
...                   ...  
3137                   56  
3138                   46  
3139                    0  
3140                  100  
3141                   66  

[3108 rows x 11 columns]

In [10]:
#//*********************************
#//*********************************
#//*** RENDER HISTORICAL GIF
#//*********************************
#//*********************************


#//*** Only Render Animated GIF if not using Cached values...ie during an update.
if not use_cached_files:

    #//********************************************
    #//*** Build Output Filepath
    #//********************************************
    filepath = os.getcwd()
    filepath = filepath.replace("\\","/")
    filepath = f"{filepath}/project/base_gif_1/"

    files_jpg = []
    gif_files = []
    #//********************************************


    plot_df = attrib_confirm_df.copy()

    fontsize=20

    dates = all_dates[100:]
    #dates = all_dates[-30:]

    first=True

    file_counter = 0
    print("Working...")
    for date in dates:

        file_counter += 1

        fig, ax = plt.subplots()

        fig.set_size_inches(10,20)
        fig = plt.gcf()
        ax.axis('off')

        #plt.title("Cumulative COVID Prevalence",fontsize=display_size)
        #fig.text(.78, .2, 'Cumulative Cases (per 100k)', va='center' ,fontsize=display_size/2)
        plot_df.plot(column=f'{date}_scaled_100k', ax=ax,linewidth=0.8,edgecolor='.8')
        plt.title(f"COVID-19 Prevalence\nNew Cases per 100,000 Population (7-Day Average)",fontsize=fontsize)
        plt.text(-120,25,date,fontsize=fontsize)
        plt.viridis()

        save_filename = f"{filepath}confirm_hist_{file_counter}.jpg"
        print(save_filename)
        plt.savefig(save_filename,quality=95)
        plt.close()

        #//*** Read Files and Prepare Animated GID
        if first == True:
            first=False
            first_img = Image.open(save_filename)
        else:
            gif_files.append(Image.open(save_filename))

    #//*** Build and Save Animated GIF
    first_img.save("confirm_100k_history.gif", save_all=True, optimize=True, append_images=gif_files, duration=50, loop=0)




    print("Done...")

In [11]:
#//*** Markdown code. But It's bogging down the system
#![](confirm_100k_history.gif)

In [12]:
attrib_confirm_df.head(5)

STATEFP  GEOID      NAME                                           geometry  Province_State                     Loc  Population  pop_100k  1/29/20_New_Cases  1/29/20_New_Cases_per_100k  \
0      37  37017    Bladen  POLYGON ((-78.90200 34.83527, -78.79960 34.850...  North Carolina  Bladen, North Carolina       32722   0.32722                  0                           0   
1      37  37167    Stanly  POLYGON ((-80.49737 35.20210, -80.29542 35.502...  North Carolina  Stanly, North Carolina       62806   0.62806                  0                           0   
2      39  39153    Summit  POLYGON ((-81.68699 41.13596, -81.68495 41.277...            Ohio            Summit, Ohio      541013   5.41013                  0                           0   
3      42  42113  Sullivan  POLYGON ((-76.81373 41.59003, -76.22014 41.541...    Pennsylvania  Sullivan, Pennsylvania        6066   0.06066                  0                           0   
4      48  48459    Upshur  POLYGON ((-95.15274 32.66095, -95.15211 32.902...           Texas           Upshur, Texas       41753   0.41753                  0                           0   

   1/29/20_scaled_100k  1/30/20_New_Cases  1/30/20_New_Cases_per_100k  1/30/20_scaled_100k  1/31/20_New_Cases  1/31/20_New_Cases_per_100k  1/31/20_scaled_100k  2/1/20_New_Cases  \
0                    0                  0                           0                    0                  0                           0                    0                 0   
1                    0                  0                           0                    0                  0                           0                    0                 0   
2                    0                  0                           0                    0                  0                           0                    0                 0   
3                    0                  0                           0                    0                  0                           0                    0                 0   
4                    0                  0                           0                    0                  0                           0                    0                 0   

   2/1/20_New_Cases_per_100k  2/1/20_scaled_100k  2/2/20_New_Cases  2/2/20_New_Cases_per_100k  2/2/20_scaled_100k  2/3/20_New_Cases  2/3/20_New_Cases_per_100k  2/3/20_scaled_100k  2/4/20_New_Cases  \
0                          0                   0                 0                          0                   0                 0                          0                   0                 0   
1                          0                   0                 0                          0                   0                 0                          0                   0                 0   
2                          0                   0                 0                          0                   0                 0                          0                   0                 0   
3                          0                   0                 0                          0                   0                 0                          0                   0                 0   
4                          0                   0                 0                          0                   0                 0                          0                   0                 0   

   2/4/20_New_Cases_per_100k  2/4/20_scaled_100k  2/5/20_New_Cases  2/5/20_New_Cases_per_100k  2/5/20_scaled_100k  2/6/20_New_Cases  2/6/20_New_Cases_per_100k  2/6/20_scaled_100k  2/7/20_New_Cases  \
0                          0                   0                 0                          0                   0                 0                          0                   0                 0   
1                          0                   0                 0                          0                   0                 0                          0                   0 

In [13]:
attrib_death_df.head(5)

STATEFP  GEOID      NAME                                           geometry  Province_State                     Loc  Population  pop_100k  1/29/20_New_Deaths  1/29/20_New_Deaths_per_100k  \
0      37  37017    Bladen  POLYGON ((-78.90200 34.83527, -78.79960 34.850...  North Carolina  Bladen, North Carolina       32722   0.32722                   0                            0   
1      37  37167    Stanly  POLYGON ((-80.49737 35.20210, -80.29542 35.502...  North Carolina  Stanly, North Carolina       62806   0.62806                   0                            0   
2      39  39153    Summit  POLYGON ((-81.68699 41.13596, -81.68495 41.277...            Ohio            Summit, Ohio      541013   5.41013                   0                            0   
3      42  42113  Sullivan  POLYGON ((-76.81373 41.59003, -76.22014 41.541...    Pennsylvania  Sullivan, Pennsylvania        6066   0.06066                   0                            0   
4      48  48459    Upshur  POLYGON ((-95.15274 32.66095, -95.15211 32.902...           Texas           Upshur, Texas       41753   0.41753                   0                            0   

   1/29/20_scaled_100k  1/30/20_New_Deaths  1/30/20_New_Deaths_per_100k  1/30/20_scaled_100k  1/31/20_New_Deaths  1/31/20_New_Deaths_per_100k  1/31/20_scaled_100k  2/1/20_New_Deaths  \
0                    0                   0                            0                    0                   0                            0                    0                  0   
1                    0                   0                            0                    0                   0                            0                    0                  0   
2                    0                   0                            0                    0                   0                            0                    0                  0   
3                    0                   0                            0                    0                   0                            0                    0                  0   
4                    0                   0                            0                    0                   0                            0                    0                  0   

   2/1/20_New_Deaths_per_100k  2/1/20_scaled_100k  2/2/20_New_Deaths  2/2/20_New_Deaths_per_100k  2/2/20_scaled_100k  2/3/20_New_Deaths  2/3/20_New_Deaths_per_100k  2/3/20_scaled_100k  \
0                           0                   0                  0                           0                   0                  0                           0                   0   
1                           0                   0                  0                           0                   0                  0                           0                   0   
2                           0                   0                  0                           0                   0                  0                           0                   0   
3                           0                   0                  0                           0                   0                  0                           0                   0   
4                           0                   0                  0                           0                   0                  0                           0                   0   

   2/4/20_New_Deaths  2/4/20_New_Deaths_per_100k  2/4/20_scaled_100k  2/5/20_New_Deaths  2/5/20_New_Deaths_per_100k  2/5/20_scaled_100k  2/6/20_New_Deaths  2/6/20_New_Deaths_per_100k  \
0                  0                           0                   0                  0                           0                   0                  0                           0   
1                  0                           0                   0                  0                           0                   0                  0                           0   
2                  0                           0         

In [14]:
#//********************************************
#//*** Build Deaths Current Stats Plot
#//********************************************
plot_df = attrib_death_df[(list(attrib_death_df.columns[:8]) + list(attrib_death_df.columns[-3:]))].copy()



category = plot_df.columns[-1]


#//*** Assign Max Scale Value 5
plot_df.loc[plot_df[category] > 5,category]=5

hover_cols = ["Loc","Population"]
hover_cols = (["Loc","Population"] + list(plot_df.columns[-3:-1]))

out_death_latest = plot_df.plot_bokeh(
    figsize=(1268, 1024),
    category=category,
    title = f"Current COVID New Death Prevalence (per 100k population) 7-Day Average\nUpdated: {all_dates[-1]}",
    #category="New_Cases_9/17/21",
    #simplify_shapes=5000,
    #dropdown=["POPESTIMATE2010", "POPESTIMATE2017"],
    #colormap="Viridis",
    #colormap="Inferno",
    colormap="Magma",
    hovertool_columns=hover_cols,
    show_figure=True,
    return_html=True
    #tile_provider_url=r"http://c.tile.stamen.com/watercolor/{Z}/{X}/{Y}.jpg"
    )



In [15]:
#//********************************************
#//*** Build Death Historical Slider Plot
#//********************************************
plot_df = attrib_death_df.copy()

#//*** Assign Max Scale Value 5
for col in [f"{x}_scaled_100k" for x in all_dates]:
    plot_df.loc[plot_df[col] > 5,col]=5

#//*** Assign Max Scale Value 100 is too much
#for col in [f"{x}_New_Deaths" for x in all_dates]:
#    plot_df.loc[plot_df[col] > 10,col]=20
#    plot_df.loc[plot_df[col] < 0,col]=0
    
    
slider_columns = [f"{x}_scaled_100k" for x in all_dates]
#slider_columns = [f"{x}_New_Deaths" for x in all_dates]

slider_range = all_dates
slider_range = [i for i in range(0,len(all_dates))]

#hover_cols = ["Population","Loc"]
#for x in [x*(int(len(all_dates)/8)) for x in range(1,9)]:
#    hover_cols.append(f"{all_dates[x]}_New_Cases")
#    hover_cols.append(f"{all_dates[x]}_New_Cases_per_100k")
hover_cols = ["Population","Loc"]

slider_name = "COVID Day"

out_death_historical = plot_df.plot_bokeh(
    figsize=(1268, 1024),
    #category="scale_100k",
    title = f"U.S. COVID Death Prevalence (Cases per 100k Population) 7-Day Average: {all_dates[0]} - {all_dates[-1]}",
    slider=slider_columns,
    slider_range = slider_range,
    slider_name = slider_name,
    #title = "TITLE HERE",
    #category="New_Cases_9/17/21",
    #simplify_shapes=5000,
    #dropdown=["POPESTIMATE2010", "POPESTIMATE2017"],
    #colormap="Viridis",
    #colormap="Inferno",
    colormap="Magma",
    hovertool_columns=hover_cols,
    show_figure=True,
    return_html=True
    #tile_provider_url=r"http://c.tile.stamen.com/watercolor/{Z}/{X}/{Y}.jpg"
    )
#plt.show()

In [16]:
#//****************************************************************************************
#//*** Copy the HTML/Javascript & Animated GIFs o the Website Production Folder
#//****************************************************************************************
directory_path = os.getcwd()

directory_path = directory_path.replace("\\","/")

#//*** Remove two sublevels to get to github root
directory_path = "".join(f"{x}/" for x in directory_path.split("/")[:-2])

#//*** Add in Fixed Relative path
directory_path += "/kstoneburner.github.io/DSC640/"

#//*** write raw HTML to output folder
with open(f"{directory_path}dash_1.raw" , "w") as f:
    f.write(out_confirm_latest)

#//*** write raw HTML to output folder
with open(f"{directory_path}dash_2.raw" , "w") as f:
    f.write(out_confirm_historical)
    
#//*** write raw HTML to output folder
with open(f"{directory_path}dash_3.raw" , "w") as f:
    f.write(out_death_latest)
    
#//*** write raw HTML to output folder
with open(f"{directory_path}dash_4.raw" , "w") as f:
    f.write(out_death_historical)
    
    
    
shutil.copyfile("confirm_100k_history.gif", f"{directory_path}confirm_100k_history.gif")
print()

In [17]:
#//****************************************************************************************
#//*** Update the HTML Template, by inserting Graph code into the template placeholders
#//*** Keeps things smooth(ish)
#//****************************************************************************************

input_template_filename = "covid_dash_v1.template.html"
output_html_filename = input_template_filename.replace(".template","")

replace_vals = {
    "$$covid_dashboard_1$$" : "dash_1.raw",
    "$$covid_dashboard_2$$" : "dash_2.raw",
    "$$covid_dashboard_3$$" : "dash_3.raw",
    "$$covid_dashboard_4$$" : "dash_4.raw",
}

#//*** Load the Template
with open(f"{directory_path}{input_template_filename}" , "r") as f:
    template_text = f.read()

#//*** Replace Each Value in Replace_vals
for find_val, replace_filename in replace_vals.items():
    with open(f"{directory_path}{replace_filename}" , "r") as f:
        
        #//*** Replace the find val (placeholder) with the HTML file
        template_text = template_text.replace(find_val,f.read())
        

#//*** Write the updated text to file
with open(f"{directory_path}{output_html_filename}" , "w") as f:
    f.write(template_text)


In [18]:
#//*** Integrate County Population From Census Bureau

#//*****************************************************
#//*** Scrape Census Population Data
#//*****************************************************
#//*** Only need to scrape once, keeping for reference
#//*****************************************************
"""
for x in range(1,57):
    x = str(x)
    if len(x) < 2:
        x = f"0{x}"
    filename = f"cc-est2019-agesex-{x}.csv"
    url = f"https://www2.census.gov/programs-surveys/popest/datasets/2010-2019/counties/asrh/{filename}"
    print(url)
    try:
        response = requests.get(url)
        if response.ok:
            print(f"Downloaded: {filename}")
            f = open(f"./demo_data/{filename}", "w")
            f.write(response.text)
            f.close()
            print(f"Written: {filename}")

    except:
        print(f"Error: {filename}")
    time.sleep(1)

print()
"""
#//*****************************************************
#//*** END Scrape
#//*****************************************************
"""
#//*** Census Data stored in individual files for each State.
#//*** Read Each State, grab the most Recent year (12).
#//*** Merge each State on County name. There are muliple counties with the same name across the country
#//*** Has to be done one county at a time.
#//*** Each State is Concatenated to a pop_df at each iteration of the loop.


pop_df = pd.DataFrame()

#//*** Get population Totals from each county

for x in range(1,57):
    
    #//*** Build Each Filename to read
    x = str(x)
    if len(x) < 2:
        x = f"0{x}"
    filename = f"./demo_data/cc-est2019-agesex-{x}.csv"
    
    #//*** There are a few number gaps, continue the loop if no file exsts
    try:
        tdf = pd.read_csv(filename)
    except:
        continue
    
    #//*** Only keep the last year
    tdf = tdf[tdf['YEAR']==12]
    
    #//*** Reformat County name to match confirmed County Name
    tdf['CTYNAME'] = tdf['CTYNAME'].str.replace(" County","")

    #//*** Keep the relevant columns
    tdf = tdf[["STNAME","CTYNAME","POPESTIMATE"]]
    
    #//*** Merge with confirmed on county names to get Dataframe with GEOID and Population estimate
    #//*** Matches the unique state name for this file with confirm_df, then performs merge for just that state on county name
    tdf = confirm_df[confirm_df["Province_State"]==tdf["STNAME"].unique()[0]][["GEOID","NAME"]].merge(tdf,left_on="NAME",right_on="CTYNAME")
    
    #//*** Delete Duplicate names Just NAME for now.
    for col in ["NAME"]:
        if col in tdf.columns:
            del tdf[col]
    
    #//*** Add State County population to pop_df which is built one state at time.
    pop_df = pd.concat([pop_df,tdf],axis=0)
"""
print()